In [2]:
!pip install inflect
!pip install PyDictionary

In [1]:
import nltk
nltk.download('stopwords')
nltk.download('punkt')
import json
import numpy as np
import pandas as pd
import re
import requests
import types


from pathlib import Path
from PyDictionary import PyDictionary
from tqdm.notebook import tqdm
from typing import Any, Dict, List, Set, Union

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Dylan\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Dylan\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
def load_basic_word_list(stopwords: Union[List[str], Set[str]] = nltk.corpus.stopwords.words('english')) -> Set[str]:
    
    stopwords = set(stopwords)  # Leverage hashing
    
    def load_ogden_basic_words(path: str) -> Set[str]:
        with open(path, 'r') as file:
            raw_words = file.read().replace('\n', ',').lower().split(',')
            
        words = []
        for raw_word in raw_words:
            word = raw_word
            for value in ['basic:', 'intl:', 'endings:', 'compound:', 'next:', '(', ')', '.']:
                word = word.replace(value, '')
            words.append(word.strip())
        return set(word for word in words if word)
            
    def load_wikipedia_words(path: str) -> Set[str]:
        with open(path, 'r') as file:
            raw_words = file.read().replace('\n', '').replace('.', '').lower().split(',')
        return set(word.strip() for word in raw_words if word)
    
    def load_espresso_verbs(path: str) -> Set[str]:
        with open(path, 'r') as file:
            raw_words = file.read().lower().split('\n')
        return set(word[3:].strip() for word in raw_words if word and len(word) > 3)
    
    def load_ef_australia_words(path: str) -> Set[str]:
        with open(path, 'r') as file:
            raw_words = file.read().lower().split('\n')
        return set(word.strip() for word in raw_words if word)
    
    basic_word_list: set = set([])
    word_list_directory = Path().resolve().parents[0] / 'data' / 'basic_word_lists'
    basic_word_lists: Dict[str, str] = {
        'ogden_basic_words.txt': load_ogden_basic_words,
        'wikipedia_words.txt': load_wikipedia_words,
#         'espresso_verbs.txt': load_espresso_verbs,
#         'ef_australia_words.txt': load_ef_australia_words,
    }
    for filename, read_function in basic_word_lists.items():
        basic_word_list |= read_function(word_list_directory / filename)
    
    return set(word for word in basic_word_list if word not in stopwords)

In [13]:
class Token:
    
    def __init__(self, token: str):
        self.string: str = token.strip()
        self.dictionary = PyDictionary(self.string)
        self.complexity_score: int = 0
            
    def __str__(self):
        return self.string
            
    def initialize_all_attributes(self, basic_word_list: Union[list, set]) -> bool:
        """Initializes all class attributes to avoid manually running down the list each time.
        
        :param Union[list, set] basic_word_list: the set of "Basic" words for self.semantic_word_complexity
        :return bool: successfully initialized everything?
        """
        self.get_semantic_word_complexity(basic_word_list)
        return True
        
    def get_semantic_word_complexity(self, basic_word_list: Union[list, set]) -> int:
        """Follows the algorithm proposed by the research paper "Estimation of Lexical Complexity using Language Semantics"
        by Nimavat and Champaneria. https://www.researchgate.net/publication/320466030
        
        :param Union[list, set] basic_word_list: the set of "Basic" words according to the proposed algorithm
        :return int: the Semantic Word Complexity Score
        """
        if self.complexity_score:
            return self.complexity_score
        
        stopwords = nltk.corpus.stopwords.words('english')
        tokens = self.get_definition_as_tokens(self.string, stopwords)
        for token in tokens:
            if token in basic_word_list:
                self.complexity_score += 1
            else:
                tokens2 = self.get_definition_as_tokens(token, stopwords)
                self.complexity_score += len(tokens2)
        return self.complexity_score
            
    def get_definition_as_tokens(self, word: str, stopwords: Union[List[str], Set[str]] = []) -> List[str]:
        """Converts the first definition for the provided word from PyDictionary into a list of individual tokens, 
        filtering out the provided stopwords.
        
        :param str word: the word to look up the definition of
        :param Union[list, set] stopwords: the words to remove from the definition 
        :return List[str]: list of all alphabetical, non-stopword tokens lowercase
        """
        tokens = []
        if definitions := self.dictionary.meaning(word):
            for pos, pos_definitions in definitions.items():
                for definition in (pos_definitions or []):
                    raw_tokens = nltk.word_tokenize(re.sub(r'\((.*?)$', '', definition))
                    tokens.extend([t.lower() for t in raw_tokens if t.lower() not in stopwords and t.isalpha()])
                    if tokens:
                        return tokens
        return tokens
    
    def to_dict(self) -> Dict[str, Dict[str, Any]]:
        """Converts all basic-type attributes from this class into a nested dictionary following the pattern:
        {'self.string': {'complexity_score': 'self.complexity_score', ...}}
        
        :return Dict[str, Any]: dictionary with all class attribute names as keys and values and values
        """
        allowed_types = (str, int, float, list, dict, set, tuple)
        as_dict = {key: value for key, value in vars(self).items() if isinstance(value, allowed_types)}
        return {as_dict.pop('string'): as_dict}
    
    def from_dict(self, as_dict: Dict[str, Dict[str, Any]]) -> bool:
        """Converts a dictionary into this class's attributes to prevent recalculate metrics every time.
        as_dict should follow the following pattern:
        {'self.string': {'complexity_score': 'self.complexity_score', ...}}
        
        :return bool: successfully initialized self attributes?
        """
        class_attributes = vars(self)
        for string, attributes in as_dict.items():
            if self.string != string.strip():
                continue
            for attribute_name, attribute_value in attributes.items():
                if attribute_name in class_attributes:
                    self.__setattr__(attribute_name, attribute_value)
            break
        else:
            raise Exception(f"The passed dictionary (as_dict) has no key in it matching self.string: {self.string}")
        return True
                
basic_word_list = load_basic_word_list()
        
t = Token('hand')
t.get_semantic_word_complexity(basic_word_list)
t.to_dict()

{'hand': {'complexity_score': 21}}

In [4]:
class TokenFeaturizer:
    
    def __init__(self, path: Union[str, None] = None):
        self.path: Union[str, Path] = path or Path().resolve() / 'all_tokens.json'
        self.all_tokens: Dict[str, Dict[str, str]] = self.load_all_tokens()
        self.average_complexity_score: float = 0.0
        self.basic_word_list: Union[List[str], Set[str]] = load_basic_word_list()
        
    def get_token_object(self, word: str) -> Token:
        """If the word is already in self.all_tokens data, will initialize a new Token object using this data and the
        Token.from_dict() method. Otherwise, create a new Token instance, initialize its attributes, and store it in
        self.all_tokens to avoid reinitialization in the future.
        
        :param str word: the word to create a Token from
        :return Token: an instance of the Token class initialized on the parameter word
        """
        token = Token(word)
        if token_data := self.all_tokens.get(word):  # Word already in all_tokens
            if all([key in token_data for key in token.to_dict().get(word, {})]):  # No new attributes in Token class
                processed_word = word.strip()
                token.from_dict({processed_word: token_data})
                return token
            
        token.initialize_all_attributes(self.basic_word_list)
        self.all_tokens.update(token.to_dict())
        return token
    
    def get_average_complexity_score(self) -> float:
        """Averages the complexity score of all non-zero complexity tokens in self.all_tokens.
        
        :return float: the average complexity score (excluding tokens with complexity score of zero)
        """
        if not self.average_complexity_score:
            non_zero_tokens = 0
            total_complexity_score = 0
            for token, token_data in self.all_tokens.items():
                if complexity_score := token_data.get('complexity_score'):
                    non_zero_tokens += 1
                    total_complexity_score += complexity_score
            self.average_complexity_score = np.round(total_complexity_score / non_zero_tokens, 2)
        return self.average_complexity_score
            
    def load_all_tokens(self) -> Dict[str, Dict[str, Any]]:
        """Converts the all_tokens.json file at self.path into a dictionary for faster hash look up.
        This dictionary prevents you from recalculating the attributes of all known tokens.

        :return Dict[str, Dict[str, Any]]: token name as a key with its associated metrics 
        """
        if not self.path.is_file():
            return {}
        with open(self.path, 'r') as file:
            return json.load(file)
        
    def save_all_tokens(self) -> Dict[str, Dict[str, Any]]:
        """Converts self.all_tokens dictionary into the all_tokens.json file at self.path.
        This JSON file allows you to load complexity scores for a large corpus to avoid the slow process of sending
        API requests and recalculating the scores for each word every time.

        :return Dict[str, Dict[str, Any]]: token name as a key with its associated metrics 
        """
        with open(self.path, 'w') as file:
            json.dump(self.all_tokens, file, indent=4)
        
            
tf = TokenFeaturizer(path=Path().resolve().parents[0] / 'data' / 'all_tokens.json')
token = tf.get_token_object('dog')
tf.save_all_tokens()

In [5]:
%%time
token = tf.get_token_object('dog')

Wall time: 0 ns


In [6]:
%%time
token = tf.get_token_object('god')

Wall time: 0 ns


In [7]:
tf.save_all_tokens()

In [8]:
def get_tokenized_sentence(sentence: str, 
                           stopwords: Union[List[str], Set[str]] = nltk.corpus.stopwords.words('english')) -> List[str]:
    """Converts the sentence str into a list of tokens, filtering our the provided stopwords.
        
    :param str sentence: the sentence string to convert
    :param Union[List[str], Set[str]] stopwords: the words to remove from the definition 
    :return List[str]: list of all alphabetical, non-stopword tokens lowercase
    """
    tokens = nltk.word_tokenize(sentence)
    return [token.lower() for token in tokens if token.lower() not in stopwords and token.isalpha()]

In [13]:
sentence = 'This is a test sentence to see how high the complexity score is.'
tokens = [Token(tok) for tok in get_tokenized_sentence(sentence)]

sentence_complexity_score = sum([token.get_semantic_word_complexity(basic_word_list) for token in tokens])
sentence_complexity_score

81

In [14]:
sentence = 'List comprehensions are one of the really nice and powerful features of Python.'
tokens = [Token(tok) for tok in get_tokenized_sentence(sentence)]
sentence_complexity_score = sum([token.get_semantic_word_complexity(basic_word_list) for token in tokens])
sentence_complexity_score

145

In [20]:
# Real Example from the Testing Data
sentence = 'A watering can is a container that is used to water plants by hand.'
tokens = [Token(tok) for tok in get_tokenized_sentence(sentence)]
sentence_complexity_scores = [token.get_semantic_word_complexity(basic_word_list) for token in tokens]
print(f"Tokens: {[str(token) for token in tokens]}")
for token in tokens:
    print(token)
    print((token.dictionary.meaning(token.string) or {'Noun': [None]}).get('Noun', [None])[0])
print(f"Complexity Scores: {sentence_complexity_scores}")
print(f"Summed Complexity Score: {sum(sentence_complexity_scores)}")

Tokens: ['watering', 'container', 'used', 'water', 'plants', 'hand']
watering
shedding tears
container
any object that can be used to hold things (especially a large metal boxlike object of standardized dimensions that can be loaded from one form of transport to another
used
None
water
binary compound that occurs at room temperature as a clear colorless odorless tasteless liquid; freezes into ice below 0 degrees centigrade and boils above 100 degrees centigrade; widely used as a solvent
plants
buildings for carrying on industrial labor
hand
the (prehensile
Complexity Scores: [12, 5, 16, 73, 26, 21]
Summed Complexity Score: 153


In [10]:
sentence = ('The legislature, the Oireachtas, consists of a lower house, Dáil Éireann, an upper house, Seanad Éireann, '
            'and an elected President (Uachtarán) who serves as the largely ceremonial head of state, but with some '
            'important powers and duties.')
tokens = [Token(tok) for tok in get_tokenized_sentence(sentence)]
sentence_complexity_score = sum([token.get_semantic_word_complexity(basic_word_list) for token in tokens])
sentence_complexity_score

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range


258

In [16]:
# FROM data_cleaning.ipynb
def remove_lrb_rrb_tags(dataframe: pd.DataFrame) -> pd.DataFrame:
    """Removes -LRB-...-RRB- tags along with all text between from 'original_text' column.
    
    Expected dataframe columns:
        original_text: str
    
    :return pd.DataFrame: the passed DataFrame cleaned
    """
    dataframe.original_text = dataframe.original_text.str.replace(r' -LRB-(.*?)-RRB-', '', regex=True)
    return dataframe

def replace_html_char_codes_with_char(dataframe: pd.DataFrame) -> pd.DataFrame:
    """Replaces char codes (e.g. &ndash;) with their respective characters.
    
    Expected dataframe columns:
        original_text: str
    
    :return pd.DataFrame: the passed DataFrame cleaned
    """ # TODO: Find/compile CSV of all codes and dynamically import and replace all
    characters: Dict[str, str] = { # Code: Character
        '&ndash;': '–',
        '&mdash;': '—',
    }
    for code, character in characters.items():
        dataframe.original_text = dataframe.original_text.str.replace(f"{code[0]} {code[1:-1]} {code[-1]}", character)
    return dataframe

def clean_dataset(dataframe: pd.DataFrame) -> pd.DataFrame:
    """Performs all required data cleaning on all records in the passed DataFrame.
    
    Expected dataframe columns:
        original_text: str
        label: int (0 or 1)
    
    :return pd.DataFrame: the passed DataFrame cleaned
    """
    cleaning_steps = [
        remove_lrb_rrb_tags,
        replace_html_char_codes_with_char,
    ]
    for cleaning in cleaning_steps:
        dataframe = cleaning(dataframe)
    return dataframe

In [17]:
tf = TokenFeaturizer(path=Path().resolve().parents[0] / 'data' / 'all_tokens.json')
token = tf.get_token_object('hand')
token.initialize_all_attributes(basic_word_list)
token.complexity_score

21

## Build all_tokens.json asset for quicker calculation of complexity scores

In [289]:
def generate_all_training_tokens() -> bool:
    training_path = Path().resolve().parents[0] / 'data' / 'WikiLarge_Train.csv'
    df = clean_dataset(pd.read_csv(training_path))
    tf = TokenFeaturizer(path=Path().resolve().parents[0] / 'data' / 'all_tokens.json')
    counter, exceptions = 0, []
    for sentence in tqdm(df.original_text):
        try:
            for token in get_tokenized_sentence(sentence):
                tf.get_token_object(token)
                
            if counter % 5 == 0:
                tf.save_all_tokens()
            counter += 1
        except Exception as e:
            print(f"Exception: {e}")
            exceptions.append(sentence)
            
    tf.save_all_tokens()
             
generate_all_training_tokens()

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: HTTPConnectionPool(host='wordnetweb.princeton.edu', port=80): Ma

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

...

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

In [291]:
def generate_all_test_tokens() -> bool:
    training_path = Path().resolve().parents[0] / 'data' / 'WikiLarge_Test.csv'
    df = clean_dataset(pd.read_csv(training_path))
    tf = TokenFeaturizer(path=Path().resolve().parents[0] / 'data' / 'all_tokens.json')
    counter, exceptions = 0, []
    for sentence in tqdm(df.original_text):
        try:
            for token in get_tokenized_sentence(sentence):
                tf.get_token_object(token)
                
            if counter % 25 == 0:
                tf.save_all_tokens()
            counter += 1
        except Exception as e:
            print(f"Exception: {e}")
            exceptions.append(sentence)
            
    tf.save_all_tokens()
             
generate_all_test_tokens()

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

...

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list index out of range
Error: The Following Error occured: list

## Prepare training dataframe

In [7]:
training_path = Path().resolve().parents[0] / 'data' / 'WikiLarge_Train.csv'
df = pd.read_csv(training_path)
df = clean_dataset(df)
df.head()

original_text  label
0  There is manuscript evidence that Austen conti...      1
1  In a remarkable comparative analysis , Mandaea...      1
2  Before Persephone was released to Hermes , who...      1
3  Cogeneration plants are commonly found in dist...      1
4  Geneva is the second-most-populous city in Swi...      1

In [22]:
def get_complexity_scores(tf: TokenFeaturizer, sentence: str) -> List[Union[int, float]]:
    """Calculates a list of complexity scores for all valid tokens in sentence. Will replace all 0 complexity scores with
    the average complexity score of all_tokens stored in the param tf.
    
    :param TokenFeaturizer tf: an initialized TokenFeaturizer instance
    :param str sentence: the sentence to calculate the complexity score of
    :return List[Union[int, float]]: all complexity scores for non-stopword tokens in sentence
    """
    return [cs if (cs := tf.get_token_object(tok).complexity_score) else tf.get_average_complexity_score()
            for tok in get_tokenized_sentence(sentence)]

tf = TokenFeaturizer(path=Path().resolve().parents[0] / 'data' / 'all_tokens.json')
#df['complexity_scores'] = df['original_text'].apply(lambda x: get_complexity_scores(tf, x))
#df.head()

In [9]:
# df['sum_cs'] = np.sum(df['complexity_scores'])
df['sum_cs'] = df['complexity_scores'].map(sum)
df.head()

original_text  label  \
0  There is manuscript evidence that Austen conti...      1   
1  In a remarkable comparative analysis , Mandaea...      1   
2  Before Persephone was released to Hermes , who...      1   
3  Cogeneration plants are commonly found in dist...      1   
4  Geneva is the second-most-populous city in Swi...      1   

                                   complexity_scores  sum_cs  
0  [13, 11, 30, 11, 8, 7, 15, 2, 17.89, 3, 3, 38,...  360.89  
1  [8, 14, 28, 52, 4, 10, 17.89, 38, 29, 5, 12, 5...  278.89  
2  [17.89, 7, 17.89, 14, 9, 17.89, 3, 6, 34, 3, 2...  181.67  
3  [17.89, 26, 4, 11, 14, 19, 40, 26, 19, 11, 15,...  441.89  
4                         [48, 26, 24, 4, 26, 17.89]  145.89

In [10]:
df['token_count'] = df['complexity_scores'].str.len()
df.head()

original_text  label  \
0  There is manuscript evidence that Austen conti...      1   
1  In a remarkable comparative analysis , Mandaea...      1   
2  Before Persephone was released to Hermes , who...      1   
3  Cogeneration plants are commonly found in dist...      1   
4  Geneva is the second-most-populous city in Swi...      1   

                                   complexity_scores  sum_cs  token_count  
0  [13, 11, 30, 11, 8, 7, 15, 2, 17.89, 3, 3, 38,...  360.89           18  
1  [8, 14, 28, 52, 4, 10, 17.89, 38, 29, 5, 12, 5...  278.89           13  
2  [17.89, 7, 17.89, 14, 9, 17.89, 3, 6, 34, 3, 2...  181.67           15  
3  [17.89, 26, 4, 11, 14, 19, 40, 26, 19, 11, 15,...  441.89           27  
4                         [48, 26, 24, 4, 26, 17.89]  145.89            6

In [11]:
df['avg_cs'] = df['sum_cs'] / df['token_count']
df.head()

original_text  label  \
0  There is manuscript evidence that Austen conti...      1   
1  In a remarkable comparative analysis , Mandaea...      1   
2  Before Persephone was released to Hermes , who...      1   
3  Cogeneration plants are commonly found in dist...      1   
4  Geneva is the second-most-populous city in Swi...      1   

                                   complexity_scores  sum_cs  token_count  \
0  [13, 11, 30, 11, 8, 7, 15, 2, 17.89, 3, 3, 38,...  360.89           18   
1  [8, 14, 28, 52, 4, 10, 17.89, 38, 29, 5, 12, 5...  278.89           13   
2  [17.89, 7, 17.89, 14, 9, 17.89, 3, 6, 34, 3, 2...  181.67           15   
3  [17.89, 26, 4, 11, 14, 19, 40, 26, 19, 11, 15,...  441.89           27   
4                         [48, 26, 24, 4, 26, 17.89]  145.89            6   

      avg_cs  
0  20.049444  
1  21.453077  
2  12.111333  
3  16.366296  
4  24.315000

In [14]:
df['text_length'] = df['original_text'].str.count(' ') + 1
df.head()

original_text  label  \
0  There is manuscript evidence that Austen conti...      1   
1  In a remarkable comparative analysis , Mandaea...      1   
2  Before Persephone was released to Hermes , who...      1   
3  Cogeneration plants are commonly found in dist...      1   
4  Geneva is the second-most-populous city in Swi...      1   

                                   complexity_scores  sum_cs  token_count  \
0  [13, 11, 30, 11, 8, 7, 15, 2, 17.89, 3, 3, 38,...  360.89           18   
1  [8, 14, 28, 52, 4, 10, 17.89, 38, 29, 5, 12, 5...  278.89           13   
2  [17.89, 7, 17.89, 14, 9, 17.89, 3, 6, 34, 3, 2...  181.67           15   
3  [17.89, 26, 4, 11, 14, 19, 40, 26, 19, 11, 15,...  441.89           27   
4                         [48, 26, 24, 4, 26, 17.89]  145.89            6   

      avg_cs  stopword_count  text_length  
0  20.049444              25           43  
1  21.453077              10           23  
2  12.111333              22           37  
3  16.366296              12           39  
4  24.315000              10           16

In [15]:
df['stopword_count'] = df['text_length'] - df['token_count']
df.head()

original_text  label  \
0  There is manuscript evidence that Austen conti...      1   
1  In a remarkable comparative analysis , Mandaea...      1   
2  Before Persephone was released to Hermes , who...      1   
3  Cogeneration plants are commonly found in dist...      1   
4  Geneva is the second-most-populous city in Swi...      1   

                                   complexity_scores  sum_cs  token_count  \
0  [13, 11, 30, 11, 8, 7, 15, 2, 17.89, 3, 3, 38,...  360.89           18   
1  [8, 14, 28, 52, 4, 10, 17.89, 38, 29, 5, 12, 5...  278.89           13   
2  [17.89, 7, 17.89, 14, 9, 17.89, 3, 6, 34, 3, 2...  181.67           15   
3  [17.89, 26, 4, 11, 14, 19, 40, 26, 19, 11, 15,...  441.89           27   
4                         [48, 26, 24, 4, 26, 17.89]  145.89            6   

      avg_cs  stopword_count  text_length  
0  20.049444              25           43  
1  21.453077              10           23  
2  12.111333              22           37  
3  16.366296              12           39  
4  24.315000              10           16

In [19]:
def process_features(df: pd.DataFrame, all_tokens_path: Union[Path, str]) -> pd.DataFrame:
    """Adds the following columns to the parameter DataFrame: [
        'text_length': int,  # length of all tokens in original_text
        'token_count': int,  # all non-stopword tokens
        'stopword_count': int,
        'complexity_scores': List[float],  # complexity scores of all non-stopword tokens (zeros replaced by average)
        'sum_cs': float,
        'avg_cs': float,
    ]
    
    :param pd.DataFrame df: required column: 'original_text': str
    :return pd.DataFrame: the original dataframe with more feature columns
    """
    tf = TokenFeaturizer(all_tokens_path)
    df['text_length'] = df['original_text'].str.count(' ') + 1
    df['complexity_scores'] = df['original_text'].apply(lambda x: get_complexity_scores(tf, x))
    df['token_count'] = df['complexity_scores'].str.len()
    df['stopword_count'] = df['text_length'] - df['token_count']
    df['sum_cs'] = df['complexity_scores'].map(sum)
    df['avg_cs'] = df['sum_cs'] / df['token_count']
    return df

In [18]:
training_path = Path().resolve().parents[0] / 'data' / 'WikiLarge_Train.csv'
df = pd.read_csv(training_path)
df = clean_dataset(df)
df = process_features(df, all_tokens_path=Path().resolve().parents[0] / 'data' / 'all_tokens.json')

In [19]:
df.head()

original_text  label  text_length  \
0  There is manuscript evidence that Austen conti...      1           43   
1  In a remarkable comparative analysis , Mandaea...      1           23   
2  Before Persephone was released to Hermes , who...      1           37   
3  Cogeneration plants are commonly found in dist...      1           39   
4  Geneva is the second-most-populous city in Swi...      1           16   

                                   complexity_scores  token_count  \
0  [13, 11, 30, 11, 8, 7, 15, 2, 17.89, 3, 3, 38,...           18   
1  [8, 14, 28, 52, 4, 10, 17.89, 38, 29, 5, 12, 5...           13   
2  [17.89, 7, 17.89, 14, 9, 17.89, 3, 6, 34, 3, 2...           15   
3  [17.89, 26, 4, 11, 14, 19, 40, 26, 19, 11, 15,...           27   
4                         [48, 26, 24, 4, 26, 17.89]            6   

   stopword_count  sum_cs     avg_cs  
0              25  360.89  20.049444  
1              10  278.89  21.453077  
2              22  181.67  12.111333  
3              12  441.89  16.366296  
4              10  145.89  24.315000

In [21]:
df.to_csv(Path().resolve().parents[0] / 'data'/ 'clean_training_data.csv')

In [22]:
df.head()

original_text  label  text_length  \
0  There is manuscript evidence that Austen conti...      1           43   
1  In a remarkable comparative analysis , Mandaea...      1           23   
2  Before Persephone was released to Hermes , who...      1           37   
3  Cogeneration plants are commonly found in dist...      1           39   
4  Geneva is the second-most-populous city in Swi...      1           16   

                                   complexity_scores  token_count  \
0  [13, 11, 30, 11, 8, 7, 15, 2, 17.89, 3, 3, 38,...           18   
1  [8, 14, 28, 52, 4, 10, 17.89, 38, 29, 5, 12, 5...           13   
2  [17.89, 7, 17.89, 14, 9, 17.89, 3, 6, 34, 3, 2...           15   
3  [17.89, 26, 4, 11, 14, 19, 40, 26, 19, 11, 15,...           27   
4                         [48, 26, 24, 4, 26, 17.89]            6   

   stopword_count  sum_cs     avg_cs  
0              25  360.89  20.049444  
1              10  278.89  21.453077  
2              22  181.67  12.111333  
3              12  441.89  16.366296  
4              10  145.89  24.315000

In [23]:
testing_path = Path().resolve().parents[0] / 'data' / 'WikiLarge_Test.csv'
df2 = pd.read_csv(testing_path)
df2 = clean_dataset(df2)
df2 = process_features(df2, all_tokens_path=Path().resolve().parents[0] / 'data' / 'all_tokens.json')

In [25]:
df2.head(99)

id                                      original_text  label  text_length  \
0    0                                              -2011    NaN            1   
1    1                                              -2011    NaN            1   
2    2                                              -2000    NaN            1   
3    3                                              -1997    NaN            1   
4    4                                              1.636    NaN            1   
..  ..                                                ...    ...          ...   
94  94  -- and King Ahab grew annoyed at such insolence .    NaN           10   
95  95             - Andrei Rublev , Russian iconographer    NaN            6   
96  96                                       '' Angels ''    NaN            3   
97  97  '' Another One Bites the Dust '' \/O/ '' Do n'...    NaN           22   
98  98                '' Another State of Mind '' -- 2:38    NaN            8   

                        complexity_scores  token_count  stopword_count  \
0                                      []            0               1   
1                                      []            0               1   
2                                      []            0               1   
3                                      []            0               1   
4                                      []            0               1   
..                                    ...          ...             ...   
94                   [12, 38, 14, 20, 21]            5               5   
95              [17.89, 17.89, 22, 17.89]            4               2   
96                                   [16]            1               2   
97  [12, 21, 10, 11, 19, 5, 17.89, 7, 10]            9              13   
98                           [12, 27, 23]            3               5   

    sum_cs     avg_cs  
0     0.00        NaN  
1     0.00        NaN  
2     0.00        NaN  
3     0.00        NaN  
4     0.00        NaN  
..     ...        ...  
94  105.00  21.000000  
95   75.67  18.917500  
96   16.00  16.000000  
97  112.89  12.543333  
98   62.00  20.666667  

[99 rows x 9 columns]

In [28]:
df2.to_csv(Path().resolve().parents[0] / 'data' / 'clean_testing_data.csv')